<a href="https://colab.research.google.com/github/andyzengmath/Coursera_Capstone/blob/main/The_Battle_of_Neighborhoods_Finding_a_Better_Place_in_Manhattan.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# IBM Applied Data Science Capstone Project: The Battle of Neighborhoods Finding a Better Place in Manhattan

## Install and import relevant libaries

In [1]:
!pip install geocoder
!pip install folium

     |████████████████████████████████| 102kB 4.6MB/s 


In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import geocoder

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


##Data Extraction and Cleaning

We use   [2014 New York City Neighborhood Names  GeoJSON data](https://https://geo.nyu.edu/catalog/nyu_2451_34572). We use can simply run a `wget` command and access the data.

In [3]:
!wget -q -O 'newyork_data.json' https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json
print('Data downloaded!')

Data downloaded!


Load and explore the data

In [4]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [6]:
# newyork_data

Extract neighborhood data from 'feature' key

In [7]:
neighborhoods_data = newyork_data['features']
neighborhoods_data[0]

{'geometry': {'coordinates': [-73.84720052054902, 40.89470517661],
  'type': 'Point'},
 'geometry_name': 'geom',
 'id': 'nyu_2451_34572.1',
 'properties': {'annoangle': 0.0,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661],
  'borough': 'Bronx',
  'name': 'Wakefield',
  'stacked': 1},
 'type': 'Feature'}

Tranform the data into a pandas dataframe

In [8]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

Take a look at first 5 lines

In [9]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [10]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


In [11]:
def neighborhood_list(grouped):    
    return ', '.join(sorted(grouped['Neighborhood'].tolist()))
                    
grp = neighborhoods.groupby(['Borough'])
df = grp.apply(neighborhood_list).reset_index(name='Neighborhood')

In [12]:
df.head()

Borough                                       Neighborhood
0          Bronx  Allerton, Baychester, Bedford Park, Belmont, B...
1       Brooklyn  Bath Beach, Bay Ridge, Bedford Stuyvesant, Ben...
2      Manhattan  Battery Park City, Carnegie Hill, Central Harl...
3         Queens  Arverne, Astoria, Astoria Heights, Auburndale,...
4  Staten Island  Annadale, Arden Heights, Arlington, Arrochar, ...

In [13]:
df.describe()

Borough                                       Neighborhood
count          5                                                  5
unique         5                                                  5
top     Brooklyn  Bath Beach, Bay Ridge, Bedford Stuyvesant, Ben...
freq           1                                                  1

In [15]:
def get_latilong(postal_code):
    lati_long_coords = None
    while(lati_long_coords is None):
        g = geocoder.arcgis('{}, New York, New York'.format(postal_code))
        lati_long_coords = g.latlng
    return lati_long_coords



Add Latitude & Longitude

In [16]:
# Retrieving Postal Code Co-ordinates
borough = df['Borough']    
coords = [ get_latilong(borough) for borough in borough.tolist() ]

In [17]:
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])
df['Latitude'] = df_coords['Latitude']
df['Longitude'] = df_coords['Longitude']

In [18]:
df.head()

Borough                                       Neighborhood  \
0          Bronx  Allerton, Baychester, Bedford Park, Belmont, B...   
1       Brooklyn  Bath Beach, Bay Ridge, Bedford Stuyvesant, Ben...   
2      Manhattan  Battery Park City, Carnegie Hill, Central Harl...   
3         Queens  Arverne, Astoria, Astoria Heights, Auburndale,...   
4  Staten Island  Annadale, Arden Heights, Arlington, Arrochar, ...   

    Latitude  Longitude  
0  40.879998 -73.882159  
1  40.678785 -73.944084  
2  40.714500 -74.006010  
3  40.752750 -73.938940  
4  40.621220 -74.129150

Use geopy library to get the latitude and longitude values of New York City.


In [19]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


Create a map of New York with neighborhoods superimposed on top.

In [20]:
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

## Map of Manhattan


Create a new dataframe of the Manhattan data

In [21]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data.head()

Borough        Neighborhood   Latitude  Longitude
0  Manhattan         Marble Hill  40.876551 -73.910660
1  Manhattan           Chinatown  40.715618 -73.994279
2  Manhattan  Washington Heights  40.851903 -73.936900
3  Manhattan              Inwood  40.867684 -73.921210
4  Manhattan    Hamilton Heights  40.823604 -73.949688

Get the geographical coordinates of Manhattan

In [22]:
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.7896239, -73.9598939.


Create a map of Manhattan, NY

In [23]:
map_manhattan = folium.Map(location=[latitude, longitude], zoom_start=11)

for lat, lng, label in zip(manhattan_data['Latitude'], manhattan_data['Longitude'], manhattan_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_manhattan)  
    
map_manhattan

Foursquare API

In [24]:
# API info
CLIENT_ID = 'CURLH5YYCXMLJUABNE5Y22LK1JNKWHZLO5MCW2OD4PRRRDK1' # my Foursquare ID
CLIENT_SECRET = 'O5PCL405KIK4MGGBIMJD2EIAYSEIQK03W4QMEG4L4ZYOEMMF' # my Foursquare Secret
VERSION = '20180604'
LIMIT = 100
print('Your credentails:')
print('CLIENT_ID: '+CLIENT_ID)
print('CLIENT_SECRET: '+CLIENT_SECRET)

Your credentails:
CLIENT_ID: CURLH5YYCXMLJUABNE5Y22LK1JNKWHZLO5MCW2OD4PRRRDK1
CLIENT_SECRET: O5PCL405KIK4MGGBIMJD2EIAYSEIQK03W4QMEG4L4ZYOEMMF


Now, let's get the top 100 venues that are in Marble Hill within a radius of 700 meters.¶


In [25]:
radius = 700 
LIMIT = 100
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    latitude, 
   longitude, 
    radius, 
   LIMIT)
results = requests.get(url).json()

In [26]:
results


{'meta': {'code': 200, 'requestId': '6092da0857ed2b69fac53e2f'},
 'response': {'groups': [{'items': [{'reasons': {'count': 0,
       'items': [{'reasonName': 'globalInteractionReason',
         'summary': 'This spot is popular',
         'type': 'general'}]},
      'referralId': 'e-0-4a78425df964a52053e51fe3-0',
      'venue': {'categories': [{'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/arts_entertainment/stadium_tennis_',
          'suffix': '.png'},
         'id': '4e39a956bd410d7aed40cbc3',
         'name': 'Tennis Court',
         'pluralName': 'Tennis Courts',
         'primary': True,
         'shortName': 'Tennis Court'}],
       'id': '4a78425df964a52053e51fe3',
       'location': {'address': 'Central Park West at 96th St',
        'cc': 'US',
        'city': 'New York',
        'country': 'United States',
        'distance': 169,
        'formattedAddress': ['Central Park West at 96th St',
         'New York, NY 10024',
         'United States'],
        'labele

In [27]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a pandas dataframe.


In [28]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


name         categories        lat  \
0           Central Park Tennis Center       Tennis Court  40.789313   
1                          East Meadow              Field  40.790160   
2       North Meadow Recreation Center  Recreation Center  40.791216   
3                    The Jewish Museum             Museum  40.785276   
4  Central Park - Wild West Playground         Playground  40.789715   

         lng  
0 -73.961862  
1 -73.955498  
2 -73.959661  
3 -73.957411  
4 -73.965471

In [29]:
# Top 10 Categories
a=pd.Series(nearby_venues.categories)
a.value_counts()[:10]

Baseball Field           13
Playground                6
Park                      4
Café                      2
French Restaurant         2
Outdoors & Recreation     1
Art Museum                1
Chinese Restaurant        1
Deli / Bodega             1
Italian Restaurant        1
Name: categories, dtype: int64

Explore nearby venues

In [30]:
def getNearbyVenues(names, latitudes, longitudes, radius=700):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # making GET request
        venue_results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in venue_results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [31]:
Manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                   latitudes=manhattan_data['Latitude'],
                                   longitudes=manhattan_data['Longitude']
                                  )

Marble Hill
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Upper West Side
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Little Italy
Soho
West Village
Manhattan Valley
Morningside Heights
Gramercy
Battery Park City
Financial District
Carnegie Hill
Noho
Civic Center
Midtown South
Sutton Place
Turtle Bay
Tudor City
Stuyvesant Town
Flatiron
Hudson Yards


In [32]:
print('There are {} Uniques Categories.'.format(len(Manhattan_venues['Venue Category'].unique())))
Manhattan_venues.groupby('Neighborhood').count().head()

There are 334 Uniques Categories.


Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                              
Battery Park City                    100                     100    100   
Carnegie Hill                        100                     100    100   
Central Harlem                        70                      70     70   
Chelsea                              100                     100    100   
Chinatown                            100                     100    100   

                   Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                        
Battery Park City             100              100             100  
Carnegie Hill                 100              100             100  
Central Harlem                 70               70              70  
Chelsea                       100              100             100  
Chinatown                     100              100             100

One Hot Encoding of Features¶


In [33]:
# one hot encoding
Manhattan_onehot = pd.get_dummies(Manhattan_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
Manhattan_onehot['Neighborhood'] = Manhattan_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [Manhattan_onehot.columns[-1]] + list(Manhattan_onehot.columns[:-1])
Manhattan_onehot = Manhattan_onehot[fixed_columns]
Manhattan_grouped = Manhattan_onehot.groupby('Neighborhood').mean().reset_index()
Manhattan_onehot.head(5)

Neighborhood  Accessories Store  Adult Boutique  African Restaurant  \
0  Marble Hill                  0               0                   0   
1  Marble Hill                  0               0                   0   
2  Marble Hill                  0               0                   0   
3  Marble Hill                  0               0                   0   
4  Marble Hill                  0               0                   0   

   American Restaurant  Animal Shelter  Antique Shop  Argentinian Restaurant  \
0                    0               0             0                       0   
1                    0               0             0                       0   
2                    0               0             0                       0   
3                    0               0             0                       0   
4                    0               0             0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0            0           0                    0                 0   
1            0           0                    0                 0   
2            0           0                    0                 0   
3            0           0                    0                 0   
4            0           0                    0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  Basketball Court  \
0          0           0       0     0    0               0                 0   
1          0           0       0     0    0               0                 0   
2          0           0       0     0    0               0                 0   
3          0           0       0     0    0               0                 0   
4          0           0       0     0    0               0                 0   

   Beer Bar  Beer Garden  Beer Store  Bike Rental / Bike Share  Bike Shop  \
0         0            0           0                         0          0   
1         0            0           0                         0          0   
2         0            0           0                         0          0   
3         0            0           0                         0          0   
4         0            0           0                         0          0   

   Bike Trail  Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  \
0           0       0           0              0          0         0   
1           0       0           0              0          0         0   
2           0       0           0              0          0         0   
3           0       0           0              0          0         0   
4           0       0           0              0          0         0   

   Boxing Gym  Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0           0                     0               0        0            0   
1           0                     0               0        0            0   
2           0                     0               0        0            0   
3           0                     0               0        0            0   
4           0                     0               0        0            0   

   Bridge  Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0       0                0         0             0              0         0   
1       0                0         0             0              0         0   
2       0                0         0             0              0         0   
3       0   

In [34]:
num_top_venues = 5
for hood in Manhattan_grouped['Neighborhood']:
    print("---- "+hood+" ----")
    temp =Manhattan_grouped[Manhattan_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

---- Battery Park City ----
                  venue  freq
0                  Park  0.11
1           Coffee Shop  0.08
2         Memorial Site  0.03
3                 Hotel  0.03
4  Gym / Fitness Center  0.03


---- Carnegie Hill ----
                  venue  freq
0                  Café  0.07
1           Coffee Shop  0.06
2  Gym / Fitness Center  0.04
3                Bakery  0.04
4           Yoga Studio  0.03


---- Central Harlem ----
                             venue  freq
0               Seafood Restaurant  0.04
1  Southern / Soul Food Restaurant  0.04
2                    Deli / Bodega  0.04
3                              Bar  0.04
4             Caribbean Restaurant  0.03


---- Chelsea ----
                 venue  freq
0          Art Gallery  0.07
1          Coffee Shop  0.06
2               Bakery  0.05
3  American Restaurant  0.04
4       Ice Cream Shop  0.03


---- Chinatown ----
                venue  freq
0  Chinese Restaurant  0.10
1              Bakery  0.08
2        Dess

In [35]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Most Common venues near neighborhood¶


In [36]:
import numpy as np
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = Manhattan_grouped['Neighborhood']

for ind in np.arange(Manhattan_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(Manhattan_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Battery Park City                  Park           Coffee Shop   
1      Carnegie Hill                  Café           Coffee Shop   
2     Central Harlem                   Bar         Deli / Bodega   
3            Chelsea           Art Gallery           Coffee Shop   
4          Chinatown    Chinese Restaurant                Bakery   

  3rd Most Common Venue            4th Most Common Venue  \
0                 Hotel                            Plaza   
1                Bakery             Gym / Fitness Center   
2    Seafood Restaurant  Southern / Soul Food Restaurant   
3                Bakery              American Restaurant   
4          Dessert Shop                     Optical Shop   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0  Gym / Fitness Center          Burger Joint         Memorial Site   
1           Yoga Studio             Bookstore          Cocktail Bar   
2             Jazz Club             Juice Bar  Gym / Fitness Center   
3     French Restaurant    Seafood Restaurant        Ice Cream Shop   
4          Cocktail Bar           Coffee Shop                   Spa   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0        Clothing Store                   Gym             Playground  
1            Art Museum           Pizza Place      French Restaurant  
2                Lounge         Grocery Store      French Restaurant  
3    Italian Restaurant                  Café                  Hotel  
4        Sandwich Place   American Restaurant         Ice Cream Shop

## Chinese restaurant

In [37]:
Manhattan_grouped.head()

Neighborhood  Accessories Store  Adult Boutique  African Restaurant  \
0  Battery Park City                0.0             0.0            0.000000   
1      Carnegie Hill                0.0             0.0            0.000000   
2     Central Harlem                0.0             0.0            0.028571   
3            Chelsea                0.0             0.0            0.000000   
4          Chinatown                0.0             0.0            0.000000   

   American Restaurant  Animal Shelter  Antique Shop  Argentinian Restaurant  \
0             0.010000             0.0           0.0                     0.0   
1             0.020000             0.0           0.0                     0.0   
2             0.028571             0.0           0.0                     0.0   
3             0.040000             0.0           0.0                     0.0   
4             0.030000             0.0           0.0                     0.0   

   Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0     0.000000        0.00                  0.0              0.00   
1     0.000000        0.03                  0.0              0.00   
2     0.014286        0.00                  0.0              0.00   
3     0.070000        0.00                  0.0              0.01   
4     0.000000        0.00                  0.0              0.02   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                0.01        0.01                   0.00                 0.00   
1                0.00        0.00                   0.00                 0.00   
2                0.00        0.00                   0.00                 0.00   
3                0.00        0.00                   0.00                 0.00   
4                0.00        0.00                   0.01                 0.01   

   BBQ Joint  Bagel Shop    Bakery  Bank       Bar  Baseball Field  \
0   0.020000    0.000000  0.000000   0.0  0.010000            0.01   
1   0.000000    0.010000  0.040000   0.0  0.020000            0.00   
2   0.014286    0.014286  0.014286   0.0  0.042857            0.00   
3   0.000000    0.010000  0.050000   0.0  0.020000            0.00   
4   0.000000    0.000000  0.080000   0.0  0.010000            0.00   

   Basketball Court  Beer Bar  Beer Garden  Beer Store  \
0               0.0  0.000000         0.01        0.00   
1               0.0  0.000000         0.00        0.01   
2               0.0  0.014286         0.00        0.00   
3               0.0  0.010000         0.00        0.00   
4               0.0  0.000000         0.00        0.00   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                       0.0       0.00         0.0    0.01         0.0   
1                       0.0       0.00         0.0    0.00         0.0   
2                       0.0       0.00         0.0    0.00         0.0   
3                       0.0       0.00         0.0    0.00         0.0   
4                       0.0       0.01         0.0    0.00         0.0   

   Boat or Ferry  Bookstore  Boutique  Boxing Gym  Brazilian Restaurant  \
0           0.01   0.010000  0.000000        0.01                   0.0   
1           0.00   0.030000  0.000000        0.00                   0.0   
2           0.00   0.014286  0.014286        0.00                   0.0   
3           0.00   0.020000  0.000000        0.00                   0.0   
4           0.00   0.010000  0.010000        0.00                   0.0   

   Breakfast Spot  Brewery  Bridal Shop  Bridge  Bubble Tea Shop  Building  \
0            0.00      0.0          0.0     0.0             0.00       0.0   
1            0.00      0.0          0.0     0.0             0.00       0.0   
2            0.00      0.0          0.0     0.0             0.00       0.0   
3            0.01      0.0          0.0     0.0             0.00       0.0   
4            0.00      0.0          0.0     0.0             0.01       0.0   

   Burger Joint

In [38]:
print(Manhattan_grouped.shape)

(40, 335)


In [39]:
len(Manhattan_grouped[Manhattan_grouped["Chinese Restaurant"] > 0])

26

In [40]:
chinese = Manhattan_grouped[["Neighborhood","Chinese Restaurant"]]
chinese.head()

Neighborhood  Chinese Restaurant
0  Battery Park City            0.000000
1      Carnegie Hill            0.010000
2     Central Harlem            0.028571
3            Chelsea            0.010000
4          Chinatown            0.100000

K_means clustering

In [41]:
from sklearn.cluster import KMeans
toclusters = 3


clustering = chinese.drop(["Neighborhood"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=toclusters, random_state=1)
kmeans.fit_transform(clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:20]

array([0, 0, 1, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 1],
      dtype=int32)

In [42]:
chinese_merged = chinese.copy()

# add clustering labels
chinese_merged["Cluster Labels"] = kmeans.labels_

In [43]:
chinese_merged

Neighborhood  Chinese Restaurant  Cluster Labels
0     Battery Park City            0.000000               0
1         Carnegie Hill            0.010000               0
2        Central Harlem            0.028571               1
3               Chelsea            0.010000               0
4             Chinatown            0.100000               2
5          Civic Center            0.020000               0
6               Clinton            0.010000               0
7           East Harlem            0.022989               0
8          East Village            0.010000               0
9    Financial District            0.000000               0
10             Flatiron            0.000000               0
11             Gramercy            0.010000               0
12    Greenwich Village            0.010000               0
13     Hamilton Heights            0.052083               1
14         Hudson Yards            0.000000               0
15               Inwood            0.020000               0
16           Lenox Hill            0.010000               0
17       Lincoln Square            0.000000               0
18         Little Italy            0.050000               1
19      Lower East Side            0.030000               1
20     Manhattan Valley            0.030000               1
21       Manhattanville            0.043478               1
22          Marble Hill            0.000000               0
23              Midtown            0.010000               0
24        Midtown South            0.000000               0
25  Morningside Heights            0.051282               1
26          Murray Hill            0.010000               0
27                 Noho            0.000000               0
28     Roosevelt Island            0.000000               0
29                 Soho            0.010000               0
30      Stuyvesant Town            0.000000               0
31         Sutton Place            0.020000               0
32              Tribeca            0.000000               0
33           Tudor City            0.000000               0
34           Turtle Bay            0.000000               0
35      Upper East Side            0.010000               0
36      Upper West Side            0.010000               0
37   Washington Heights            0.020000               0
38         West Village            0.020000               0
39            Yorkville            0.000000               0

In [44]:
to_merged = chinese_merged.join(Manhattan_venues.set_index("Neighborhood"), on="Neighborhood")

print(to_merged.shape)
to_merged.head()

(3769, 9)


Neighborhood  Chinese Restaurant  Cluster Labels  \
0  Battery Park City                 0.0               0   
0  Battery Park City                 0.0               0   
0  Battery Park City                 0.0               0   
0  Battery Park City                 0.0               0   
0  Battery Park City                 0.0               0   

   Neighborhood Latitude  Neighborhood Longitude  \
0              40.711932              -74.016869   
0              40.711932              -74.016869   
0              40.711932              -74.016869   
0              40.711932              -74.016869   
0              40.711932              -74.016869   

                                Venue  Venue Latitude  Venue Longitude  \
0         Battery Park City Esplanade       40.711622       -74.017907   
0                         Hudson Eats       40.712666       -74.015901   
0     Institute of Culinary Education       40.712399       -74.015971   
0  Waterfront Plaza, Brookfield Place       40.713241       -74.016241   
0            Equinox Brookfield Place       40.712704       -74.014995   

   Venue Category  
0            Park  
0      Food Court  
0  Cooking School  
0           Plaza  
0             Gym

In [45]:
to_merged.sort_values(["Cluster Labels"], inplace=True)
to_merged.head()

Neighborhood  Chinese Restaurant  Cluster Labels  \
0   Battery Park City                 0.0               0   
28   Roosevelt Island                 0.0               0   
28   Roosevelt Island                 0.0               0   
28   Roosevelt Island                 0.0               0   
28   Roosevelt Island                 0.0               0   

    Neighborhood Latitude  Neighborhood Longitude  \
0               40.711932              -74.016869   
28              40.762160              -73.949168   
28              40.762160              -73.949168   
28              40.762160              -73.949168   
28              40.762160              -73.949168   

                          Venue  Venue Latitude  Venue Longitude  \
0   Battery Park City Esplanade       40.711622       -74.017907   
28                         NISI       40.761915       -73.949966   
28   Roosevelt Island Promenade       40.760875       -73.952437   
28         East Side River Walk       40.765391       -73.951725   
28               Manhattan Park       40.765540       -73.947075   

           Venue Category  
0                    Park  
28       Greek Restaurant  
28  Outdoors & Recreation  
28             Waterfront  
28                   Park

In [46]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(toclusters)
ys = [i + x + (i*x)**2 for i in range(toclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(to_merged['Neighborhood Latitude'], to_merged['Neighborhood Longitude'], to_merged['Neighborhood'], to_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [47]:
#Cluster 0
to_merged.loc[(to_merged['Cluster Labels'] ==0) & (to_merged['Venue Category'] == 'Chinese Restaurant') ]

Neighborhood  Chinese Restaurant  Cluster Labels  \
31        Sutton Place            0.020000               0   
31        Sutton Place            0.020000               0   
29                Soho            0.010000               0   
23             Midtown            0.010000               0   
26         Murray Hill            0.010000               0   
37  Washington Heights            0.020000               0   
37  Washington Heights            0.020000               0   
36     Upper West Side            0.010000               0   
38        West Village            0.020000               0   
38        West Village            0.020000               0   
35     Upper East Side            0.010000               0   
8         East Village            0.010000               0   
6              Clinton            0.010000               0   
7          East Harlem            0.022989               0   
7          East Harlem            0.022989               0   
11            Gramercy            0.010000               0   
1        Carnegie Hill            0.010000               0   
3              Chelsea            0.010000               0   
5         Civic Center            0.020000               0   
5         Civic Center            0.020000               0   
15              Inwood            0.020000               0   
15              Inwood            0.020000               0   
12   Greenwich Village            0.010000               0   
16          Lenox Hill            0.010000               0   

    Neighborhood Latitude  Neighborhood Longitude                      Venue  \
31              40.760280              -73.963556                     Hutong   
31              40.760280              -73.963556                   Mr. Chow   
29              40.722184              -74.000657      Joe’s Steam Rice Roll   
23              40.754691              -73.981669         Xi’an Famous Foods   
26              40.748303              -73.978332                 Café China   
37              40.851903              -73.936900   No. 1 Chinese Restaurant   
37              40.851903              -73.936900                Yang Garden   
36              40.787658              -73.977059                Han Dynasty   
38              40.734434              -74.006180                      Decoy   
38              40.734434              -74.006180                    RedFarm   
35              40.775639              -73.960508                 Pig Heaven   
8               40.727847              -73.982226               Málà Project   
6               40.759101              -73.996119              Panda Express   
7               40.792249              -73.944182          Steak and Hoagies   
7               40.792249              -73.944182                 Moon House   
11              40.737210              -73.981376                       Milu   
1               40.782683              -73.953256                     Wok 88   
3               40.744035              -74.003116                   Buddakan   
5               40.715229              -74.005415  Tonii’s Fresh Rice Noodle   
5               40.715229              -74.005415      Joe’s Steam Rice Roll   
15              40.867684              -73.921210              Lotus Express   
15              40.867684              -73.921210                   "U" Like   
12              40.726933              -73.999914                 Chow House   
16              40.768113              -73.958860                   Shanghai   

    Venue Latitude  Venue Longitude      Venue Category  
31       40.761365       -73.967592  Chinese Restaurant  
31       40.758703       -73.964552  Chinese Restaurant  
29       40.718852       -74.001025  Chinese Restaurant  
23       40.754969       -73.982497  Chinese Restaurant  
26       40.749980       -73.982234  Chinese Restaurant  
37       40.851237       -73.939606  Chinese Restaurant  
37       40.855309       -73.937832  Chinese Restaur

In [49]:
to_merged.loc[(to_merged['Cluster Labels'] ==1) & (to_merged['Venue Category'] == 'Chinese Restaurant') ]

Neighborhood  Chinese Restaurant  Cluster Labels  \
19      Lower East Side            0.030000               1   
19      Lower East Side            0.030000               1   
2        Central Harlem            0.028571               1   
2        Central Harlem            0.028571               1   
18         Little Italy            0.050000               1   
18         Little Italy            0.050000               1   
18         Little Italy            0.050000               1   
19      Lower East Side            0.030000               1   
18         Little Italy            0.050000               1   
18         Little Italy            0.050000               1   
13     Hamilton Heights            0.052083               1   
13     Hamilton Heights            0.052083               1   
21       Manhattanville            0.043478               1   
21       Manhattanville            0.043478               1   
13     Hamilton Heights            0.052083               1   
13     Hamilton Heights            0.052083               1   
21       Manhattanville            0.043478               1   
13     Hamilton Heights            0.052083               1   
25  Morningside Heights            0.051282               1   
25  Morningside Heights            0.051282               1   
25  Morningside Heights            0.051282               1   
25  Morningside Heights            0.051282               1   
20     Manhattan Valley            0.030000               1   
20     Manhattan Valley            0.030000               1   
20     Manhattan Valley            0.030000               1   

    Neighborhood Latitude  Neighborhood Longitude  \
19              40.717807              -73.980890   
19              40.717807              -73.980890   
2               40.815976              -73.943211   
2               40.815976              -73.943211   
18              40.719324              -73.997305   
18              40.719324              -73.997305   
18              40.719324              -73.997305   
19              40.717807              -73.980890   
18              40.719324              -73.997305   
18              40.719324              -73.997305   
13              40.823604              -73.949688   
13              40.823604              -73.949688   
21              40.816934              -73.957385   
21              40.816934              -73.957385   
13              40.823604              -73.949688   
13              40.823604              -73.949688   
21              40.816934              -73.957385   
13              40.823604              -73.949688   
25              40.808000              -73.963896   
25              40.808000              -73.963896   
25              40.808000              -73.963896   
25              40.808000              -73.963896   
20              40.797307              -73.964286   
20              40.797307              -73.964286   
20              40.797307              -73.964286   

                                     Venue  Venue Latitude  Venue Longitude  \
19                            Happy Family       40.714449       -73.987511   
19                                 3 Times       40.718284       -73.985202   
2                    88 Chinese Restaurant       40.813187       -73.941467   
2                    Crispy Bamboo Village       40.816278       -73.946938   
18                   Joe’s Steam Rice Roll       40.718852       -74.001025   
18       Wah Fung Number 1 Fast Food 華豐快餐店       40.717278       -73.994177   
18                Yi Ji Shi Mo Noodle Corp       40.718254       -73.995930   
19                   Kings County Imperial       40.717817       -73.985569   
18                      Xi'an Famous Foods       40.715232       -73.997263   
18                           Spicy Village       40.717010       -73.993530   
13                              Golden Wok       40.826960       -73.946401   
13                              King's Wok   

In [50]:
to_merged.loc[(to_merged['Cluster Labels'] ==2) & (to_merged['Venue Category'] == 'Chinese Restaurant') ]


Neighborhood  Chinese Restaurant  Cluster Labels  Neighborhood Latitude  \
4    Chinatown                 0.1               2              40.715618   
4    Chinatown                 0.1               2              40.715618   
4    Chinatown                 0.1               2              40.715618   
4    Chinatown                 0.1               2              40.715618   
4    Chinatown                 0.1               2              40.715618   
4    Chinatown                 0.1               2              40.715618   
4    Chinatown                 0.1               2              40.715618   
4    Chinatown                 0.1               2              40.715618   
4    Chinatown                 0.1               2              40.715618   
4    Chinatown                 0.1               2              40.715618   

   Neighborhood Longitude                              Venue  Venue Latitude  \
4              -73.994279           Yi Ji Shi Mo Noodle Corp       40.718254   
4              -73.994279                           Hwa Yuan       40.713618   
4              -73.994279                   Big Wong King 大旺       40.716196   
4              -73.994279         Deluxe Green Bo Restaurant       40.715545   
4              -73.994279          Tonii’s Fresh Rice Noodle       40.715671   
4              -73.994279                 Noodle Village 粥麵軒       40.714128   
4              -73.994279                 Xi'an Famous Foods       40.715232   
4              -73.994279  Wah Fung Number 1 Fast Food 華豐快餐店       40.717278   
4              -73.994279                      Spicy Village       40.717010   
4              -73.994279          Sun Hing Lung Ho Fun Tofu       40.712968   

   Venue Longitude      Venue Category  
4       -73.995930  Chinese Restaurant  
4       -73.995978  Chinese Restaurant  
4       -73.998303  Chinese Restaurant  
4       -73.998137  Chinese Restaurant  
4       -73.999074  Chinese Restaurant  
4       -73.998746  Chinese Restaurant  
4       -73.997263  Chinese Restaurant  
4       -73.994177  Chinese Restaurant  
4       -73.993530  Chinese Restaurant  
4       -73.995149  Chinese Restaurant